In [117]:
# Set up the workspace
using SumOfSquares, JuMP, PolyJuMP, DynamicPolynomials, MultivariatePolynomials
using Mosek#, CSDP#, SCS
using Plots
gr()

include("../src/NormalSoS.jl")
using NormalSoS

include("../src/MinimumActionPath.jl")
using MAP

include("../src/GeomMinActPath.jl")
using gMAM

# Nonlinear Examples

We will examine some nonlinear examples on which the SOS decomposition method is applied.

In [2]:
# A 1D system with a quartic potential
@polyvar x;    x = [x];
F1(X::Vector) = [X[1] - X[1]^3 + 0.1];
f1 = F1(x);
@time U1 = NormalSoS.normdecomp(f1,x, MosekSolver(),1)
NormalSoS.checknorm(f1,U1,x)

Chosen basis as:
DynamicPolynomials.Monomial{true}[x^4, x^3, x^2, x, 1]
Problem
  Name                   :                 
  Objective sense        : min             
  Type                   : CONIC (conic optimization problem)
  Constraints            : 61              
  Cones                  : 0               
  Scalar variables       : 6               
  Matrix variables       : 2               
  Integer variables      : 0               

Optimizer started.
Presolve started.
Linear dependency checker started.
Linear dependency checker terminated.
Eliminator - tries                  : 0                 time                   : 0.00            
Lin. dep.  - tries                  : 1                 time                   : 0.00            
Lin. dep.  - number                 : 0               
Presolve terminated. Time: 0.00    
Problem
  Name                   :                 
  Objective sense        : min             
  Type                   : CONIC (conic optimization pro

status = :Stall
bnd = DynamicPolynomials.Monomial{true}[x^4]
getvalue(ϵ) = [0.249956]
Problem
  Name                   :                 
  Objective sense        : min             
  Type                   : CONIC (conic optimization problem)
  Constraints            : 69              
  Cones                  : 0               
  Scalar variables       : 7               
  Matrix variables       : 3               
  Integer variables      : 0               

Optimizer started.
Presolve started.
Linear dependency checker started.
Linear dependency checker terminated.
Eliminator - tries                  : 0                 time                   : 0.00            
Lin. dep.  - tries                  : 1                 time                   : 0.00            
Lin. dep.  - number                 : 0               
Presolve terminated. Time: 0.00    
Problem
  Name                   :                 
  Objective sense        : min             
  Type                   : CONIC (conic op

 34.938550 seconds (11.88 M allocations: 615.357 MiB, 1.11% gc time)


4.262620047637489e-6

In [3]:
@show(U1);

U1 = 0.24999920733223643x^4 - 0.5000041733816547x^2 - 0.09999942258906444x + 28505.193348376823


In [3]:
# A 2D quartic system from Zhou et al (2012)
@polyvar x[1:2]
F2(X::Vector) = [-1.0 + 9.0X[1] - 2.0X[1]^3 + 9.0X[2] - 2.0X[2]^3;
      1.0 - 11.0X[1] + 2.0X[1]^3 + 11.0X[2] - 2.0X[2]^3];
f2 = F2(x);
@time Ueg2 = NormalSoS.normdecomp(f2,x, MosekSolver(),1)

Chosen basis as:
DynamicPolynomials.Monomial{true}[x1^4, x1^3x2, x1^2x2^2, x1x2^3, x2^4, x1^3, x1^2x2, x1x2^2, x2^3, x1^2, x1x2, x2^2, x1, x2, 1]
Problem
  Name                   :                 
  Objective sense        : min             
  Type                   : CONIC (conic optimization problem)
  Constraints            : 594             
  Cones                  : 0               
  Scalar variables       : 18              
  Matrix variables       : 2               
  Integer variables      : 0               

Optimizer started.
Presolve started.
Linear dependency checker started.
Linear dependency checker terminated.
Eliminator - tries                  : 0                 time                   : 0.00            
Lin. dep.  - tries                  : 1                 time                   : 0.00            
Lin. dep.  - number                 : 0               
Presolve terminated. Time: 0.00    
Problem
  Name                   :                 
  Objective sense        :

x1^4 + x1^2x2^2 + x2^4
getvalue(ϵ) = [0.220945, 0.560384, 0.214877]
Problem
  Name                   :                 
  Objective sense        : min             
  Type                   : CONIC (conic optimization problem)
  Constraints            : 621             
  Cones                  : 0               
  Scalar variables       : 17              
  Matrix variables       : 3               
  Integer variables      : 0               

Optimizer started.
Presolve started.
Linear dependency checker started.
Linear dependency checker terminated.
Eliminator - tries                  : 0                 time                   : 0.00            
Lin. dep.  - tries                  : 1                 time                   : 0.00            
Lin. dep.  - number                 : 0               
Presolve terminated. Time: 0.00    
Problem
  Name                   :                 
  Objective sense        : min             
  Type                   : CONIC (conic optimization problem

0.5000000043330644x1^4 + 0.5000000078114762x2^4 - 4.999999972977872x1^2 + 0.999999824171771x1x2 - 4.999999897900875x2^2 + 0.9999999600165587x1 + 428.8074466955952

In [ ]:
# The Maier-Stein model
γ = 10.0;    μ = 1.0;
@polyvar x[1:2]
F(X::Vector) = [X[1] - X[1]^3 - γ*X[1]X[2]^2;
                 -μ*(X[1]^2 + 1)X[2]];
f = F(x);
V = -0.5*x[1]^2 + 0.25*x[1]^4 + 0.5γ*x[2]^2 + 0.5γ*x[1]^2*x[2]^2;
@time U = NormalSoS.normdecomp(f,x, MosekSolver(),2)
# NormalSoS.checknorm(f3,U3,x)

fg = -differentiate(U,x)
Fg(X::Vector) = [Float64(subs(fg[1],x[1]=>X[1], x[2]=>X[2]));
                 Float64(subs(fg[2],x[1]=>X[1], x[2]=>X[2]))];
fc = f + differentiate(U,x)
Fc(X::Vector) = [Float64(subs(fc[1],x[1]=>X[1], x[2]=>X[2]));
                 Float64(subs(fc[2],x[1]=>X[1], x[2]=>X[2]))];

In [ ]:
fg = -differentiate(U3,x);
plt3 = NormalSoS.plotlandscape(f3,U3,x,([-2 2],[-2 2]),true);    plot(plt3)

In [22]:
# Obtain the minimum action path
x₀ = [-1.0 0.0];  # Start point (row vector)
xₑ = [1.0 0.0];
Tspan = 50.0;  # Time span
N = 400;
φ₀ = MAP.makepath(x₀,xₑ,N);
for ii=1:N-2
    φ₀[ii,2] = 0.1;
end

σ = 0.1;
G(X::Vector) = σ*[1.0; 1.0];

# Use Optim to optimise over path φ
resObj = MAP.optimalpath(F,G, x₀,xₑ, Tspan,N, φ₀);
res = Optim.minimizer(resObj);

Optimisation for T=50.00 gives S=34.03
Optimisation is not converged, rerunning...
Optimisation for T=50.00 gives S=34.03
Optimisation is not converged, rerunning...
Optimisation for T=50.00 gives S=34.03
Optimisation is not converged, rerunning...
Optimisation for T=50.00 gives S=34.03
Optimisation is not converged, rerunning...
Optimisation for T=50.00 gives S=34.03
Optimisation is not converged, rerunning...
Optimisation for T=50.00 gives S=34.03
Optimisation is not converged, rerunning...
Optimisation for T=50.00 gives S=34.03
Optimisation is not converged, rerunning...
Optimisation for T=50.00 gives S=34.03
Optimisation is not converged, rerunning...
Optimisation for T=50.00 gives S=34.03
Optimisation is not converged, rerunning...
Optimisation for T=50.00 gives S=34.03
Optimisation is not converged, rerunning...
Optimisation for T=50.00 gives S=34.03
Optimisation not converged


In [32]:
dt = 0.001;    M=10000;
φ = zeros(Float64,M,2);
φ[1,:] = res[120,:]; #[-0.01 0.01];# res[1,:];
for ii=2:M
    φ[ii,:] = φ[ii-1,:] + (-Fc(φ[ii-1,:])+Fg(φ[ii-1,:]))dt;
    # println((Fc(φ[ii,:])-Fg(φ[ii,:]))dt)
end

mapPlt = plot(res[:,1],res[:,2], line=2, marker=0, label="MAP")
plot!(mapPlt, φ[:,1],φ[:,2], line=2, marker=0,label="SoS")

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 -1.5 
 
 
 -1.0 
 
 
 -0.5 
 
 
 0.0 
 
 
 0.5 
 
 
 1.0 
 
 
 0.0 
 
 
 0.2 
 
 
 0.4 
 
 
 0.6 
 
 
 0.8 
 
<polyline clip-path="url(#clip5402)" style="stroke:#009af9; stroke-width:2; stroke-opacity:1; fill:none" points="
 150.789,365.565 150.789,365.565 150.789,365.565 150.789,365.565 150.789,365.565 150.789,365.565 150.789,365.565 150.789,365.565 150.789,365.565 150.789,365.565 
 150.789,365.565 150.789,365.565 150.789,365.565 150.789,365.565 150.789,365.565 150.789,365.565 150.789,365.565 150.789,365.565 150.789,365.565 150.789,365.565 
 150.789,365.565 150.789,365.565 150.789,365.565 150.789,365.565 150.789,365.565 150.789,365.565 150.789,365.565 150.789,365.565 150.789,365.565 150.789,365.565 
 150.789,365.565 150.789,365.564 150.789,365.564 150.789,365.564 150.79,365.564 150.79,365.563 150.79,365.563 150.79,365.562 150.79,365.561 150.79,365.56 
 150.791,365.558 150.791,365.556 150.791,365.553 150.792,365.55 150.793,365.546 150.794,365.54 150.795,365.533 150.797,365.524 150.799,365.512 150.802,365.497 
 150.806,365.478 150.811,365.453 150.817,365.421 150.825,365.379 150.835,365.326 150.848,365.258 150.865,365.171 150.887,365.058 150.915,364.914 150.951,364.729 
 150.998,364.492 151.058,364.188 151.135,363.799 151.236,363.302 151.365,362.668 151.533,361.861 151.75,360.836 152.033,359.539 152.401,357.906 152.882,355.859 
 153.51,353.312 154.334,350.17 155.413,346.335 156.827,341.713 158.674,336.23 161.072,329.842 164.158,322.558 168.074,314.453 172.958,305.682 178.916,296.475 
 186.002,287.126 194.196,277.976 203.394,269.376 213.409,261.669 223.992,255.162 234.858,250.111 245.719,246.71 256.31,245.073 266.418,245.231 275.89,247.123 
 284.635,250.596 292.616,255.425 299.839,261.33 306.336,268.005 312.155,275.153 317.353,282.499 321.985,289.814 326.106,296.918 329.768,303.682 333.018,310.019 
 335.899,315.883 338.451,321.253 340.71,326.133 342.708,330.539 344.475,334.498 346.037,338.04 347.417,341.2 348.635,344.012 349.711,346.511 350.662,348.727 
 351.5,350.69 352.241,352.428 352.894,353.965 353.471,355.324 353.98,356.525 354.429,357.586 354.826,358.522 355.176,359.35 355.484,360.08 355.757,360.725 
 355.997,361.294 356.209,361.796 356.396,362.239 356.561,362.63 356.707,362.976 356.835,363.28 356.949,363.549 357.049,363.786 357.137,363.995 357.215,364.18 
 357.284,364.343 357.345,364.487 357.398,364.614 357.445,364.726 357.487,364.824 357.524,364.912 357.556,364.988 357.585,365.056 357.61,365.116 357.632,365.169 
 357.652,365.216 357.669,365.257 357.685,365.293 357.698,365.325 357.71,365.353 357.721,365.378 357.73,365.4 357.738,365.42 357.745,365.437 357.752,365.452 
 357.757,365.465 357.762,365.477 357.767,365.487 357.771,365.496 357.774,365.505 357.777,365.512 357.78,365.518 357.782,365.524 357.784,365.528 357.786,365.533 
 357.788,365.537 357.789,365.54 357.79,365.543 357.791,365.546 357.792,365.548 357.793,365.55 357.794,365.552 357.795,365.553 357.795,365.555 357.796,365.556 
 357.796,365.557 357.797,365.558 357.797,365.559 357.797,365.56 357.798,365.56 357.798,365.561 357.798,365.561 357.798,365.562 357.798,365.562 357.799,365.563 
 357.799,365.563 357.799,365.563 357.799,365.563 357.799,365.564 357.799,365.564 357.799,365.564 357.799,365.564 357.799,365.564 357.799,365.564 357.799,365.564 
 357.799,365.564 357.799,365.565 357.799,365.565 357.799,365.565 357.8,365.565 357.8,365.565 357.8,365.565 357.8,365.565 357.8,365.565 357.8,365.565 
 357.8,365.565 357.8,365.565 357.8,365.565 357.8,365.565 357.8,365.565 357.8,365.565 357.8,365.565 357.8,365.565 357.8,365.565 357.8,365.565 
 357.8,365.565 357.8,365.565 357.8,365.565 357.8,365.565 357.8,365.565 357.801,365.565 357.801,365.565 357.801,365.565 357.801,365.565 357.801,365.565 
 357.801,365.565 357.802,365.565 357.802,365.565 357.802,365.565 357.803,365.565 357.803,365.565 357.803,365.565 357.804,365.565 357.804,365.565 357.805,365.565 
 357.806

In [76]:
## Example 1: Quadratic system from Zhou et al (2012)
@polyvar x[1:2]
F(X::Vector) = [-X[1] + 2.0X[2]^2;
                -X[1]*X[2] - 2.0X[2]];
f = F(x);
@time U = NormalSoS.normdecomp(f,x, MosekSolver(),2);

fg = -differentiate(U,x)
Fg(X::Vector) = [Float64(subs(fg[1],x[1]=>X[1], x[2]=>X[2]));
                 Float64(subs(fg[2],x[1]=>X[1], x[2]=>X[2]))];
fc = f + differentiate(U,x)
Fc(X::Vector) = [Float64(subs(fc[1],x[1]=>X[1], x[2]=>X[2]));
                 Float64(subs(fc[2],x[1]=>X[1], x[2]=>X[2]))];

plt = NormalSoS.plotlandscape(f,U,x,([-3 3],[-3 3]),true);    plot(plt)
NormalSoS.checknorm(f,U,x)

Chosen basis as:
DynamicPolynomials.Monomial{true}[x1^2, x1x2, x2^2, x1, x2, 1]
Problem
  Name                   :                 
  Objective sense        : min             
  Type                   : CONIC (conic optimization problem)
  Constraints            : 101             
  Cones                  : 0               
  Scalar variables       : 8               
  Matrix variables       : 2               
  Integer variables      : 0               

Optimizer started.
Presolve started.
Linear dependency checker started.
Linear dependency checker terminated.
Eliminator started.
Freed constraints in eliminator : 1
Eliminator terminated.
Eliminator - tries                  : 1                 time                   : 0.00            
Lin. dep.  - tries                  : 1                 time                   : 0.00            
Lin. dep.  - number                 : 0               
Presolve terminated. Time: 0.00    
Problem
  Name                   :                 
  Objective s

  1.046886 seconds (467.35 k allocations: 24.630 MiB, 1.07% gc time)


1.1840151081798922e-9

In [102]:
# Obtain the minimum action path
x₀ = [0.0 0.0];  # Start point (row vector)
xₑ = [-0.5 -1.0];
Tspan = 50.0;  # Time span
N = 500;
φ₀ = MAP.makepath(x₀,xₑ,N);

σ = 0.1;
G(X::Vector) = σ*[1.0; 1.0];

# Use Optim to optimise over path φ
resObj = MAP.optimalpath(F,G, x₀,xₑ, Tspan,N, φ₀);
res = [x₀; Optim.minimizer(resObj); xₑ];

Optimisation for T=50.00 gives S=225.00
Optimisation is converged.


In [109]:
dt = 0.001;    M=10000;
φ = zeros(Float64,M,2);
φ[1,:] = res[end,:]; #[-0.5 0.5];# res[1,:];
for ii=2:M
    φ[ii,:] = φ[ii-1,:] + (-Fc(φ[ii-1,:])+Fg(φ[ii-1,:]))dt;
    # println((Fc(φ[ii,:])-Fg(φ[ii,:]))dt)
end

mapPlt = plot(φ₀[:,1],φ₀[:,2], line=2, marker=0, label="Initial")
plot!(mapPlt, res[:,1],res[:,2], line=2, marker=0,label="MAP")
plot!(mapPlt, φ[:,1],φ[:,2], line=2, marker=0,label="SoS")

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 -0.6 
 
 
 -0.5 
 
 
 -0.4 
 
 
 -0.3 
 
 
 -0.2 
 
 
 -0.1 
 
 
 0.0 
 
 
 -1.00 
 
 
 -0.75 
 
 
 -0.50 
 
 
 -0.25 
 
 
 0.00 
 
<polyline clip-path="url(#clip8202)" style="stroke:#009af9; stroke-width:2; stroke-opacity:1; fill:none" points="
 564.402,22.8028 563.606,23.4911 562.809,24.1794 562.013,24.8677 561.217,25.5559 560.42,26.2442 559.624,26.9325 558.827,27.6208 558.031,28.309 557.235,28.9973 
 556.438,29.6856 555.642,30.3739 554.846,31.0622 554.049,31.7504 553.253,32.4387 552.457,33.127 551.66,33.8153 550.864,34.5035 550.068,35.1918 549.271,35.8801 
 548.475,36.5684 547.678,37.2567 546.882,37.9449 546.086,38.6332 545.289,39.3215 544.493,40.0098 543.697,40.698 542.9,41.3863 542.104,42.0746 541.308,42.7629 
 540.511,43.4512 539.715,44.1394 538.919,44.8277 538.122,45.516 537.326,46.2043 536.529,46.8925 535.733,47.5808 534.937,48.2691 534.14,48.9574 533.344,49.6457 
 532.548,50.3339 531.751,51.0222 530.955,51.7105 530.159,52.3988 529.362,53.087 528.566,53.7753 527.77,54.4636 526.973,55.1519 526.177,55.8402 525.38,56.5284 
 524.584,57.2167 523.788,57.905 522.991,58.5933 522.195,59.2815 521.399,59.9698 520.602,60.6581 519.806,61.3464 519.01,62.0347 518.213,62.7229 517.417,63.4112 
 516.621,64.0995 515.824,64.7878 515.028,65.476 514.231,66.1643 513.435,66.8526 512.639,67.5409 511.842,68.2292 511.046,68.9174 510.25,69.6057 509.453,70.294 
 508.657,70.9823 507.861,71.6705 507.064,72.3588 506.268,73.0471 505.472,73.7354 504.675,74.4237 503.879,75.1119 503.082,75.8002 502.286,76.4885 501.49,77.1768 
 500.693,77.865 499.897,78.5533 499.101,79.2416 498.304,79.9299 497.508,80.6182 496.712,81.3064 495.915,81.9947 495.119,82.683 494.323,83.3713 493.526,84.0595 
 492.73,84.7478 491.933,85.4361 491.137,86.1244 490.341,86.8127 489.544,87.5009 488.748,88.1892 487.952,88.8775 487.155,89.5658 486.359,90.254 485.563,90.9423 
 484.766,91.6306 483.97,92.3189 483.174,93.0072 482.377,93.6954 481.581,94.3837 480.784,95.072 479.988,95.7603 479.192,96.4485 478.395,97.1368 477.599,97.8251 
 476.803,98.5134 476.006,99.2017 475.21,99.8899 474.414,100.578 473.617,101.266 472.821,101.955 472.025,102.643 471.228,103.331 470.432,104.02 469.635,104.708 
 468.839,105.396 468.043,106.084 467.246,106.773 466.45,107.461 465.654,108.149 464.857,108.838 464.061,109.526 463.265,110.214 462.468,110.902 461.672,111.591 
 460.876,112.279 460.079,112.967 459.283,113.655 458.486,114.344 457.69,115.032 456.894,115.72 456.097,116.409 455.301,117.097 454.505,117.785 453.708,118.473 
 452.912,119.162 452.116,119.85 451.319,120.538 450.523,121.227 449.727,121.915 448.93,122.603 448.134,123.291 447.338,123.98 446.541,124.668 445.745,125.356 
 444.948,126.044 444.152,126.733 443.356,127.421 442.559,128.109 441.763,128.798 440.967,129.486 440.17,130.174 439.374,130.862 438.578,131.551 437.781,132.239 
 436.985,132.927 436.189,133.616 435.392,134.304 434.596,134.992 433.799,135.68 433.003,136.369 432.207,137.057 431.41,137.745 430.614,138.433 429.818,139.122 
 429.021,139.81 428.225,140.498 427.429,141.187 426.632,141.875 425.836,142.563 425.04,143.251 424.243,143.94 423.447,144.628 422.65,145.316 421.854,146.005 
 421.058,146.693 420.261,147.381 419.465,148.069 418.669,148.758 417.872,149.446 417.076,150.134 416.28,150.822 415.483,151.511 414.687,152.199 413.891,152.887 
 413.094,153.576 412.298,154.264 411.501,154.952 410.705,155.64 409.909,156.329 409.112,157.017 408.316,157.705 407.52,158.394 406.723,159.082 405.927,159.77 
 405.131,160.458 404.334,161.147 403.538,161.835 402.742,162.523 401.945,163.211 401.149,163.9 400.352,164.588 399.556,165.276 398.76,165.965 397.963,166.653 
 397.167,167.341 396.371,168.029 395.574,168.718 394.778,169.406 393.982,170.094 393.185,170.783 392.389,171.471 391.593,172.159 390.796,172.847 390,173.536 
 389.203,174.224 388.407,174.912 387.611,175.6 386.814,176.289 386.018,176.977 385.222,177.665 384.425,178.354

In [120]:
σ = 1.0;
# Sm = gMAM.action(flipdim(φ,1),F,G,500,2);
Sm = gMAM.action(φ,F,G,500,2);
Su = Float64(subs(U,x[1]=>xₑ[1],x[2]=>xₑ[2])) - Float64(subs(U,x[1]=>x₀[1],x[2]=>x₀[2]));
@show(Sm);    @show(Su);
Sm/Su

Sm = 1.7986832352173732
Su = 1.1250000007992105


1.5988295412796194

In [128]:
dt = 0.001;    M=10000;
φ = zeros(Float64,M,2);
φ[1,:] = [0.0 0.6];
for ii=2:M
    φ[ii,:] = φ[ii-1,:] + (-Fc(φ[ii-1,:])+Fg(φ[ii-1,:]))dt;
    # println((Fc(φ[ii,:])-Fg(φ[ii,:]))dt)
end
Sm = gMAM.action(φ,F,G,500,2);
Su = Float64(subs(U,x[1]=>φ[1,1],x[2]=>φ[1,2])) - Float64(subs(U,x[1]=>φ[end,1],x[2]=>φ[end,2]));
@show(Sm);    @show(Su);
@show(Sm/Su);
plot(φ[:,1],φ[:,2])

Sm = 0.25093500560968474
Su = 0.36000000020219813
Sm / Su = 0.6970416818576228


<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 -0.100 
 
 
 -0.075 
 
 
 -0.050 
 
 
 -0.025 
 
 
 0.000 
 
 
 0.1 
 
 
 0.2 
 
 
 0.3 
 
 
 0.4 
 
 
 0.5 
 
<polyline clip-path="url(#clip0202)" style="stroke:#009af9; stroke-width:1; stroke-opacity:1; fill:none" points="
 580.315,11.811 576.77,12.5391 573.242,13.2661 569.732,13.9918 566.239,14.7163 562.764,15.4397 559.307,16.1618 555.867,16.8827 552.444,17.6025 549.038,18.3211 
 545.65,19.0384 542.278,19.7546 538.924,20.4696 535.587,21.1834 532.266,21.896 528.962,22.6074 525.676,23.3176 522.405,24.0266 519.152,24.7344 515.915,25.441 
 512.694,26.1465 509.49,26.8507 506.303,27.5538 503.131,28.2556 499.976,28.9563 496.837,29.6558 493.714,30.3541 490.607,31.0512 487.516,31.7471 484.441,32.4418 
 481.382,33.1354 478.339,33.8277 475.311,34.5189 472.3,35.2089 469.303,35.8977 466.322,36.5853 463.357,37.2717 460.407,37.9569 457.473,38.641 454.553,39.3239 
 451.649,40.0055 448.761,40.686 445.887,41.3654 443.028,42.0435 440.184,42.7205 437.356,43.3962 434.542,44.0708 431.743,44.7442 428.958,45.4165 426.188,46.0875 
 423.433,46.7574 420.693,47.4261 417.967,48.0937 415.255,48.76 412.558,49.4252 409.875,50.0892 407.206,50.7521 404.552,51.4137 401.912,52.0742 399.286,52.7335 
 396.673,53.3917 394.075,54.0487 391.491,54.7045 388.921,55.3591 386.364,56.0126 383.821,56.6649 381.292,57.316 378.777,57.966 376.275,58.6148 373.787,59.2625 
 371.312,59.909 368.85,60.5543 366.402,61.1985 363.967,61.8415 361.546,62.4833 359.137,63.124 356.742,63.7636 354.36,64.402 351.991,65.0392 349.635,65.6753 
 347.292,66.3102 344.961,66.9439 342.644,67.5766 340.339,68.208 338.047,68.8383 335.767,69.4675 333.501,70.0955 331.246,70.7224 329.005,71.3481 326.775,71.9727 
 324.558,72.5961 322.354,73.2184 320.162,73.8396 317.982,74.4596 315.814,75.0785 313.658,75.6962 311.514,76.3128 309.383,76.9283 307.263,77.5426 305.155,78.1558 
 303.06,78.7679 300.976,79.3788 298.904,79.9886 296.843,80.5973 294.794,81.2048 292.757,81.8112 290.732,82.4165 288.718,83.0207 286.715,83.6237 284.724,84.2256 
 282.745,84.8264 280.776,85.4261 278.819,86.0246 276.873,86.6221 274.939,87.2184 273.015,87.8136 271.103,88.4077 269.202,89.0007 267.312,89.5925 265.432,90.1833 
 263.564,90.7729 261.707,91.3614 259.86,91.9489 258.024,92.5352 256.199,93.1204 254.384,93.7045 252.581,94.2875 250.787,94.8694 249.005,95.4502 247.232,96.0299 
 245.471,96.6085 243.719,97.186 241.979,97.7624 240.248,98.3378 238.528,98.912 236.818,99.4851 235.118,100.057 233.428,100.628 231.748,101.198 230.079,101.767 
 228.419,102.334 226.77,102.901 225.13,103.467 223.5,104.031 221.88,104.594 220.27,105.157 218.67,105.718 217.079,106.278 215.498,106.837 213.927,107.395 
 212.365,107.952 210.813,108.508 209.27,109.063 207.737,109.616 206.214,110.169 204.699,110.721 203.194,111.271 201.698,111.821 200.212,112.369 198.735,112.916 
 197.267,113.463 195.808,114.008 194.358,114.552 192.917,115.095 191.486,115.637 190.063,116.178 188.649,116.718 187.244,117.257 185.848,117.795 184.461,118.332 
 183.083,118.868 181.713,119.402 180.352,119.936 179,120.469 177.657,121 176.322,121.531 174.995,122.06 173.677,122.589 172.368,123.116 171.067,123.643 
 169.775,124.168 168.49,124.693 167.215,125.216 165.947,125.738 164.688,126.26 163.437,126.78 162.194,127.299 160.959,127.817 159.733,128.335 158.514,128.851 
 157.304,129.366 156.101,129.88 154.907,130.393 153.72,130.906 152.542,131.417 151.371,131.927 150.208,132.436 149.053,132.944 147.906,133.451 146.766,133.957 
 145.634,134.463 144.51,134.967 143.393,135.47 142.284,135.972 141.183,136.473 140.089,136.973 139.003,137.472 137.924,137.97 136.852,138.468 135.788,138.964 
 134.731,139.459 133.682,139.953 132.639,140.446 131.605,140.939 130.577,141.43 129.556,141.92 128.543,142.41 127.537,142.898 126.538,143.385 125.546,143.872 
 124.561,144.357 123.583,144.842 122.612,145.325 121.648,145.808 120.69,146.289 119.74,146.77 118.797,147.249 117.86,147.728 116.93,148.206 1

In [112]:
plot(φ[:,1])
plot!(φ[:,2])

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 2000 
 
 
 4000 
 
 
 6000 
 
 
 8000 
 
 
 10000 
 
 
 -1.0 
 
 
 -0.8 
 
 
 -0.6 
 
 
 -0.4 
 
 
 -0.2 
 
<polyline clip-path="url(#clip8602)" style="stroke:#009af9; stroke-width:1; stroke-opacity:1; fill:none" points="
 39.502,193.84 39.5561,194.386 39.6102,194.928 39.6643,195.466 39.7184,195.999 39.7724,196.529 39.8265,197.054 39.8806,197.575 39.9347,198.093 39.9888,198.606 
 40.0429,199.115 40.097,199.62 40.1511,200.121 40.2051,200.618 40.2592,201.112 40.3133,201.601 40.3674,202.087 40.4215,202.568 40.4756,203.046 40.5297,203.52 
 40.5837,203.99 40.6378,204.456 40.6919,204.918 40.746,205.377 40.8001,205.832 40.8542,206.283 40.9083,206.73 40.9624,207.174 41.0164,207.614 41.0705,208.051 
 41.1246,208.483 41.1787,208.913 41.2328,209.338 41.2869,209.76 41.341,210.178 41.395,210.593 41.4491,211.005 41.5032,211.412 41.5573,211.817 41.6114,212.217 
 41.6655,212.615 41.7196,213.009 41.7737,213.399 41.8277,213.786 41.8818,214.17 41.9359,214.55 41.99,214.927 42.0441,215.301 42.0982,215.671 42.1523,216.038 
 42.2063,216.402 42.2604,216.762 42.3145,217.12 42.3686,217.473 42.4227,217.824 42.4768,218.172 42.5309,218.516 42.585,218.857 42.639,219.195 42.6931,219.53 
 42.7472,219.862 42.8013,220.191 42.8554,220.516 42.9095,220.839 42.9636,221.158 43.0177,221.475 43.0717,221.788 43.1258,222.099 43.1799,222.406 43.234,222.71 
 43.2881,223.012 43.3422,223.31 43.3963,223.606 43.4503,223.899 43.5044,224.189 43.5585,224.476 43.6126,224.76 43.6667,225.041 43.7208,225.319 43.7749,225.595 
 43.829,225.868 43.883,226.138 43.9371,226.405 43.9912,226.669 44.0453,226.931 44.0994,227.19 44.1535,227.446 44.2076,227.7 44.2616,227.951 44.3157,228.199 
 44.3698,228.445 44.4239,228.687 44.478,228.928 44.5321,229.165 44.5862,229.401 44.6403,229.633 44.6943,229.863 44.7484,230.09 44.8025,230.315 44.8566,230.538 
 44.9107,230.757 44.9648,230.975 45.0189,231.19 45.0729,231.402 45.127,231.612 45.1811,231.819 45.2352,232.024 45.2893,232.227 45.3434,232.427 45.3975,232.625 
 45.4516,232.821 45.5056,233.014 45.5597,233.204 45.6138,233.393 45.6679,233.579 45.722,233.763 45.7761,233.944 45.8302,234.123 45.8842,234.3 45.9383,234.475 
 45.9924,234.647 46.0465,234.817 46.1006,234.985 46.1547,235.151 46.2088,235.315 46.2629,235.476 46.3169,235.635 46.371,235.792 46.4251,235.947 46.4792,236.1 
 46.5333,236.251 46.5874,236.399 46.6415,236.546 46.6955,236.69 46.7496,236.832 46.8037,236.973 46.8578,237.111 46.9119,237.247 46.966,237.381 47.0201,237.513 
 47.0742,237.643 47.1282,237.771 47.1823,237.897 47.2364,238.021 47.2905,238.144 47.3446,238.264 47.3987,238.382 47.4528,238.498 47.5068,238.613 47.5609,238.726 
 47.615,238.836 47.6691,238.945 47.7232,239.052 47.7773,239.157 47.8314,239.26 47.8855,239.362 47.9395,239.461 47.9936,239.559 48.0477,239.655 48.1018,239.749 
 48.1559,239.841 48.21,239.932 48.2641,240.021 48.3181,240.108 48.3722,240.193 48.4263,240.277 48.4804,240.359 48.5345,240.439 48.5886,240.517 48.6427,240.594 
 48.6968,240.669 48.7508,240.743 48.8049,240.814 48.859,240.884 48.9131,240.953 48.9672,241.02 49.0213,241.085 49.0754,241.149 49.1294,241.211 49.1835,241.271 
 49.2376,241.33 49.2917,241.387 49.3458,241.443 49.3999,241.497 49.454,241.55 49.5081,241.601 49.5621,241.65 49.6162,241.698 49.6703,241.745 49.7244,241.79 
 49.7785,241.833 49.8326,241.875 49.8867,241.916 49.9407,241.955 49.9948,241.993 50.0489,242.029 50.103,242.064 50.1571,242.097 50.2112,242.129 50.2653,242.159 
 50.3194,242.188 50.3734,242.216 50.4275,242.243 50.4816,242.267 50.5357,242.291 50.5898,242.313 50.6439,242.334 50.698,242.354 50.752,242.372 50.8061,242.389 
 50.8602,242.404 50.9143,242.419 50.9684,242.432 51.0225,242.443 51.0766,242.454 51.1307,242.463 51.1847,242.47 51.2388,242.477 51.2929,242.482 51.347,242.486 
 51.4011,242.489 51.4552,242.491 51.5093,242.491 51.5633,242.49 51.6174,242.488 51.6715,242.485 51.7256,242.48 51.7797,242.475 51.8338,242.468 51.88